In [1]:
import pandas
import xml.etree.ElementTree as ET
import os
import csv
import re
%matplotlib inline
import numpy as np
import pandas as pd
import librosa as lb
import librosa.display
import matplotlib.pyplot as plt
from gensim.models import Word2Vec

## Declarations

In [3]:
read_viseme_mod = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/viseme_modified'
audio_dir = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/raw_audio'
csv_file = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/mfcc_feature_set.csv'
read_directory = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/viseme'
write_directory = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/viseme_modified'
words_list = []
viseme_text_features = []



In [2]:
viseme_set = list()
transcript_set = list()
viseme_feature_set = list()

## Functions

In [2]:
def read_csv(file_name):
    file = open(file_name)
    df = pandas.read_csv(file_name)
    return df

    

In [3]:
def read_bml(file_name):
    tree = ET.parse(file_name)
    root = tree.getroot()
    return root
    

In [4]:
def read_viseme(root):
    viseme_l = list()
    for child in root:
        viseme = list()
        if(child.tag == "lips"):
            viseme.append(child.attrib['viseme'])
            viseme.append(child.attrib['start'])
            viseme.append(child.attrib['end'])
            viseme_l.append(viseme)
    return viseme_l
            

In [5]:
def read_transcript(root,end_time):
    for child in root:
        if(child.tag=='speech'):
            for child2 in child:
                if(child2.tag == 'text'):
                    texttag = child2
                    break
    transcript_l = list()
    next_t =0
    for i,sync in enumerate(texttag):
        transcript = list()
        for t in sync:
            print(t)
        if sync.text is None : 
            transcript.append('000')
        else:    
            transcript.append(sync.text)
#         transcript.append(prev)
        transcript.append(sync.attrib['time'])
        if(i<len(texttag)-1):
            transcript.append(texttag[i+1].attrib['time'])
        else:
            transcript.append(end_time)
        
        prev = sync.attrib['time']
        transcript_l.append(transcript)
    return transcript_l

In [6]:
def get_mfcc(filename,viseme_extract):
    mfcc_l = list()
    for rec in viseme_extract:
        try:
            mfcc = create_mfcc(filename,float(rec[1]),float(rec[2])).tolist()
            mfcc.append(rec[0])
            mfcc_l.append(mfcc)
        except:
            pass
    return mfcc_l

In [7]:
def create_mfcc(audio_path, start_ms, end_ms):
    start = start_ms/100
    end = end_ms/100
    data, sample_rate = lb.load(audio_path, offset = start, duration = end - start)
    mfcc = librosa.feature.mfcc(y=data, sr=sample_rate)
    mfccScaled = np.mean(mfcc.T, axis=0)
    return mfccScaled

In [13]:
def feature_generation(audio_gen):
    for filename in os.listdir(read_viseme_mod):
        file_path_read = os.path.join(read_viseme_mod, filename)
        f_r = open(file_path_read,'r+')
        root = read_bml(f_r)
        viseme_extract = read_viseme(root)
        f_split = filename.split("_")
        audio_session = f_split[0][4]
        if(len(f_split)==4):
            audio_file_dir = f_split[0]+"_"+f_split[1]+"_"+f_split[2]
        else:
            audio_file_dir = f_split[0]+"_"+f_split[1]
        audio_file_name = filename.split(".")[0]+".wav"
        audio_path = audio_dir + "/Session" + audio_session + "/sentences/wav/"+audio_file_dir+"/"+audio_file_name
        if(audio_gen):
            mfcc_= get_mfcc(audio_path,viseme_extract)
            with open(csv_file,'a') as f:
                csv_write = csv.writer(f)
                csv_write.writerows(mfcc_)
                csv_write.writerow(list('\n'))
            viseme_feature_set.append(mfcc_)
        viseme_set.append(viseme_extract)
        transcript_set.append(read_transcript(root,viseme_extract[len(viseme_extract)-1][2]) )


In [ ]:
def textual_features(text_map,viseme_map):
    merge_set = []
    for i in range(0, len(viseme_map)):
        tmp = []   
        start_time = float(viseme_map[i][1])
        for j in range(0, len(text_map)-1):
            if float(text_map[j][1]) <= start_time < float(text_map[j+1][1]):
                tmp.append((viseme_map[i][0], text_map[j][0], viseme_map[i][1], viseme_map[i][2]))
        if not tmp:
            tmp.append((viseme_map[i][0], '000', viseme_map[i][1], viseme_map[i][2]))
        merge_set.append(tmp[0])
        words = merge_set[i][1]
        if(words is not None):
            words = words.lower()
            words_list.append(words)
    return merge_set

## Modify files 

In [9]:
# for filename in os.listdir(read_directory):
#     file_path_read = os.path.join(read_directory, filename)
#     file_path_write = os.path.join(write_directory, filename)
#     f_r = open(file_path_read,'r+')
#     f_w = open(file_path_write,'w+')
#     lines = f_r.readlines()
#     for line in lines:
#         if(re.match('.*sync.*',line)):
#             line= line.replace('/','')
#             line = line.replace('\n','')
#             line = line + '</sync>\n'
#             f_w.write(line)
#         else:
#             f_w.write(line)
#     f_r.close()
#     f_w.close()

## Read BML files

In [14]:
feature_generation(False)

In [15]:
viseme_set

[[['_', '0', '0.29'],
  ['H', '0.29', '0.36'],
  ['Ah', '0.36', '0.46'],
  ['BMP', '0.46', '0.56'],
  ['_', '0.56', '1.75']],
 [['_', '0', '1.2'],
  ['Ah', '1.2', '1.285'],
  ['Ih', '1.285', '1.37'],
  ['Aa', '1.37', '1.4'],
  ['L', '1.4', '1.43'],
  ['BMP', '1.43', '1.49'],
  ['Ow', '1.49', '1.59'],
  ['Z', '1.59', '1.69'],
  ['D', '1.69', '1.71'],
  ['Kg', '1.71', '1.73'],
  ['Aa', '1.73', '1.83'],
  ['D', '1.83', '1.84'],
  ['BMP', '1.84', '1.92'],
  ['Ah', '1.92', '2.06'],
  ['R', '2.06', '2.08'],
  ['Ih', '2.08', '2.16'],
  ['D', '2.16', '2.17'],
  ['D', '2.17', '2.32'],
  ['W', '2.32', '2.39'],
  ['Sh', '2.39', '2.44'],
  ['Ih', '2.44', '2.52'],
  ['R', '2.52', '2.56'],
  ['Z', '2.56', '2.73'],
  ['_', '2.73', '2.79'],
  ['Ah', '2.79', '2.82'],
  ['Kg', '2.82', '2.84'],
  ['Ow', '2.84', '2.87'],
  ['_', '2.87', '4.023']],
 [['_', '0', '0.05'],
  ['Ah', '0.05', '0.29'],
  ['D', '0.29', '0.4'],
  ['D', '0.4', '0.48'],
  ['_', '0.48', '0.51'],
  ['Th', '0.51', '0.58'],
  ['Ah', '0.5

In [16]:
transcript_set

[[['Hmm', '0.29', '0.56'], ['000', '0.56', '1.75']],
 [['I', '1.2', '1.37'],
  ['000', '1.37', '1.37'],
  ['almost', '1.37', '1.71'],
  ['000', '1.71', '1.71'],
  ['got', '1.71', '1.84'],
  ['000', '1.84', '1.84'],
  ['married', '1.84', '2.17'],
  ['000', '2.17', '2.17'],
  ['two', '2.17', '2.39'],
  ['000', '2.39', '2.39'],
  ['years', '2.39', '2.73'],
  ['000', '2.73', '2.79'],
  ['ago', '2.79', '2.87'],
  ['000', '2.87', '4.023']],
 [['and', '0.05', '0.48'],
  ['000', '0.48', '0.51'],
  ['the', '0.51', '0.63'],
  ['000', '0.63', '0.63'],
  ['fact', '0.63', '0.94'],
  ['000', '0.94', '0.97'],
  ['that', '0.97', '1.23'],
  ['000', '1.23', '1.64'],
  ['you', '1.64', '1.88'],
  ['000', '1.88', '1.88'],
  ['know', '1.88', '1.96'],
  ['000', '1.96', '1.96'],
  ['there', '1.96', '2.06'],
  ['000', '2.06', '2.06'],
  ['is', '2.06', '2.18'],
  ['000', '2.18', '2.18'],
  ['always', '2.18', '2.5'],
  ['000', '2.5', '2.5'],
  ['different', '2.5', '2.76'],
  ['000', '2.76', '2.76'],
  ['types', 

## Total number of viseme classes

In [17]:
vis_dict = dict()

In [18]:
for i in viseme_set:
    for j in i:
        if(j[0] not in vis_dict):
            vis_dict[j[0]] = 1

In [19]:
len(vis_dict)

21

## Own word2vec

In [22]:
for i, elem in enumerate(transcript_set):
    s = textual_features(transcript_set[i],viseme_set[i])
    viseme_text_features.append(s)


In [23]:
viseme_text_features

[[('_', '000', '0', '0.29'),
  ('H', 'Hmm', '0.29', '0.36'),
  ('Ah', 'Hmm', '0.36', '0.46'),
  ('BMP', 'Hmm', '0.46', '0.56'),
  ('_', '000', '0.56', '1.75')],
 [('_', '000', '0', '1.2'),
  ('Ah', 'I', '1.2', '1.285'),
  ('Ih', 'I', '1.285', '1.37'),
  ('Aa', 'almost', '1.37', '1.4'),
  ('L', 'almost', '1.4', '1.43'),
  ('BMP', 'almost', '1.43', '1.49'),
  ('Ow', 'almost', '1.49', '1.59'),
  ('Z', 'almost', '1.59', '1.69'),
  ('D', 'almost', '1.69', '1.71'),
  ('Kg', 'got', '1.71', '1.73'),
  ('Aa', 'got', '1.73', '1.83'),
  ('D', 'got', '1.83', '1.84'),
  ('BMP', 'married', '1.84', '1.92'),
  ('Ah', 'married', '1.92', '2.06'),
  ('R', 'married', '2.06', '2.08'),
  ('Ih', 'married', '2.08', '2.16'),
  ('D', 'married', '2.16', '2.17'),
  ('D', 'two', '2.17', '2.32'),
  ('W', 'two', '2.32', '2.39'),
  ('Sh', 'years', '2.39', '2.44'),
  ('Ih', 'years', '2.44', '2.52'),
  ('R', 'years', '2.52', '2.56'),
  ('Z', 'years', '2.56', '2.73'),
  ('_', '000', '2.73', '2.79'),
  ('Ah', 'ago', '2.7

In [24]:
sentences = []
for filename in os.listdir(read_viseme_mod):
    file_path_read = os.path.join(read_viseme_mod, filename)
    f_r = open(file_path_read,'r+')
    root = read_bml(f_r)
    script = read_transcript(root,0)
    sent = []
    for data in script :
        sent.append(data[0])
    sentences.append(sent)

In [25]:
model = Word2Vec(sentences, min_count=1,vector_size= 50,workers=3)                 
model.save("word2vec.model")       


In [26]:
model = Word2Vec.load("word2vec.model")

In [27]:
vocabulary = model.wv.key_to_index

## Merge Set

In [77]:
csv_file_text = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/textual_feature_set_new.csv'
fo = open(csv_file_text,'a')
csv_write = csv.writer(fo)
for sent in viseme_text_features:
    for tup in sent:
        word_vec = model.wv[tup[1]]
        
        word_vec = word_vec.tolist()
        word_vec.append(tup[0])
        csv_write.writerows([word_vec])
    csv_write.writerow([0]*51)
    

In [31]:
csv_file_text = '/Users/bidishadasbaksi/Docs_no_icloud/Documents – Bidisha’s MacBook Pro/ Personal_docs Intuit Laptop/USC Journey/Spring 2022/CSCI-535 Multimodal/Project/segmented/feature_combined.csv'
fo = open(csv_file_text,'a')
csv_write = csv.writer(fo)
count=0
for filename in os.listdir(read_viseme_mod):
    file_path_read = os.path.join(read_viseme_mod, filename)
    f_r = open(file_path_read,'r+')
    root = read_bml(f_r)
    viseme_extract = read_viseme(root)
    f_split = filename.split("_")
    audio_session = f_split[0][4]
    if(len(f_split)==4):
        audio_file_dir = f_split[0]+"_"+f_split[1]+"_"+f_split[2]
    else:
        audio_file_dir = f_split[0]+"_"+f_split[1]
    audio_file_name = filename.split(".")[0]+".wav"
    audio_path = audio_dir + "/Session" + audio_session + "/sentences/wav/"+audio_file_dir+"/"+audio_file_name
    s = textual_features(read_transcript(root,viseme_extract[len(viseme_extract)-1][2]),viseme_extract)
    mfcc_= get_mfcc(audio_path,viseme_extract)
    for i,data in enumerate(mfcc_):
        m_s = data[:-1] + model.wv[s[i][1]].tolist()
        viseme = data[-1]
        m_s.append(viseme)
        csv_write.writerows([m_s])
    csv_write.writerow([0]*71)       
        

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=247
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=78
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=215
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=258
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=116
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=232
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=98
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=57
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=75
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=188
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/py

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=213
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=191
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=284
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=239
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=311
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=147
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=1015
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=280
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=107
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=342
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/li

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=357
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=184
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=36
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=47
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=333
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/p

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=395
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=414
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=524
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=454
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=446
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=388
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=346
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=844
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=468
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=721
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=487
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=568
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=286
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=570
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=685
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib

/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=596
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=815
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=662
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=436
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib/python3.8/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=424
  return f(*args, **kwargs)
/Users/bidishadasbaksi/opt/anaconda3/lib